# Orbit plots in 3D

Illustrate how 3D orbits can be animated. Note that the calculation of the orbits is purely for illustration purposes; they are not right! 

Some more information on animation is available here: https://alexgude.com/blog/matplotlib-blitting-supernova/

In [8]:
import datetime
now = datetime.datetime.now()
print("Date and time",str(now))
#
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
#
# Can't use inline matplotlib backend for animations, so try TkAgg
import matplotlib
matplotlib.use('TkAgg')
#
# Set seed if want to have same sequence of random numbers every run
#np.random.seed(137)
#
# Rotation matrix elements
def Rx(theta):
    return np.matrix([[ 1, 0            , 0            ],
                      [ 0, np.cos(theta),-np.sin(theta)],
                      [ 0, np.sin(theta), np.cos(theta)]])
#
def Ry(theta):
    return np.matrix([[ np.cos(theta), 0, np.sin(theta)],
                      [ 0            , 1, 0            ],
                      [-np.sin(theta), 0, np.cos(theta)]])
# 
def Rz(theta):
    return np.matrix([[ np.cos(theta), -np.sin(theta), 0 ],
                      [ np.sin(theta), np.cos(theta) , 0 ],
                      [ 0            , 0             , 1 ]])
#
# Calculate n_planets orbits
n_frames = 50
radii = np.array([0.6, 0.8, 1.1, 1.2, 1.5, 1.9, 2.2])
#radii = np.array([0.6, 1.5])
#
# Make sure run for enough time to complete largest orbit (don't leave a gap!)
time = (n_frames + 2)*np.amax(np.sqrt(radii**3))/n_frames
n_planets = len(radii)
print(" ")
print(f"Number of planets {n_planets}, time simulated {time:.2f}")
#
# Define figure
fig = plt.figure(figsize = (8, 8))
ax = fig.add_subplot(1, 1, 1, projection = '3d')
#
# Set the axis properties
ax.set_xlim(-np.amax(radii), np.amax(radii))
ax.set_ylim(-np.amax(radii), np.amax(radii))
ax.set_zlim(-1.0, 1.0)
ax.set_xlabel('x')
ax.set_xlabel('y')
ax.set_zlabel('z')
#
# Add sun to plot
ax.plot(0, 0, 0, marker = '.', markersize = 20, color = 'yellow')
#
def update_lines_zip(num, orbits, lines):
    '''
    Update the lines in the plot, using zip to ensure that the orbits and lines are coreclty associated.
    '''
    for line, orbit in zip(lines, orbits):
        line.set_data(orbit[:num, :2].T)
        line.set_3d_properties(orbit[:num, 2])
    return lines
#
def update_lines(num, orbits, lines):
    '''
    Update the lines in the plot, using a for loop to ensure that the orbits and lines are coreclty associated.
    '''
    for n in range(0, len(lines)):
        lines[n].set_data(orbits[n][:num, :2].T)
        lines[n].set_3d_properties(orbits[n][:num, 2])
    return lines
#
def orbit(n_orbit, n_frames = 10, time = 2, radius = 1.0):
    '''
    Return a 3D "orbit" in an array with dimensions (n_frames, 3)
    '''
    t_step = time/n_frames
    period = np.sqrt(radius**3)
    omega = 2*np.pi/period
    #
    start = np.random.random(1)[0]
    alpha = 2*np.pi*(np.random.random(1)[0] - 0.5)/15.0
    beta = 2*np.pi*(np.random.random(1)[0] - 0.5)/15.0
    gamma = 2*np.pi*(np.random.random(1)[0] - 0.5)/2000.0
    #
    R = Rx(alpha)*Ry(beta)*Rz(gamma)
    #
    print(" ")
    print(f"Orbit {n_orbit}")
    print(f"Radius {radius:.2f}, angular freq. {omega:.2f}")
    print(f"Euler angles {alpha:.2f}, {beta:.2f} and {gamma:.2f}")
    print(f"Start time {start:.2f}")
    print("Rotation matrix \n",np.around(R, 3))
    #
    path = np.zeros((n_frames, 3))
    for n in range(0, n_frames):
        t = n*t_step
        flat = np.array([radius*np.cos(omega*(t - start)), radius*np.sin(omega*(t - start)), 0.0])
        tilt = np.matmul(R, flat)
        #
        # matmul returns a 1D matrix 
        path[n, :] = tilt[0, :]
    #
    return path
#
#orbit_test = orbit(0)
#print(" ")
#print("orbit_test \n",np.around(orbit_test, 2))
#
# Create empty lines and make orbits 
lines = []
orbits = []
for n in range(0, n_planets):
    lines.append(ax.plot([], [], [])[0])
    orbits.append(orbit(n, n_frames, time, radii[n]))
#
# Make animation and save as gif. Arguments here are: 
# figure name, function called for each frame, number of frames, 
# arguments passed to function, delay between frames (in ms)
ani = animation.FuncAnimation(fig, update_lines, fargs = (orbits, lines), 
                              frames = range(0, n_frames), interval = 100, blit = True)
#
# Save the animation (need to have imagemagick installed!)
ani.save('orbit.gif', writer = 'imagemagick')
#
plt.show()
#
then = now
now = datetime.datetime.now()
print("Date and time",str(now))
print("Time since last check is",str(now - then))

Date and time 2023-03-22 15:24:53.788287
 
Number of planets 7, time simulated 3.39
 
Orbit 0
Radius 0.60, angular freq. 13.52
Euler angles -0.09, 0.05 and 0.00
Start time 0.39
Rotation matrix 
 [[ 0.999 -0.001  0.053]
 [-0.003  0.996  0.086]
 [-0.053 -0.086  0.995]]
 
Orbit 1
Radius 0.80, angular freq. 8.78
Euler angles -0.19, 0.02 and -0.00
Start time 0.56
Rotation matrix 
 [[ 1.     0.001  0.017]
 [-0.004  0.983  0.184]
 [-0.016 -0.184  0.983]]
 
Orbit 2
Radius 1.10, angular freq. 5.45
Euler angles -0.11, -0.08 and -0.00
Start time 0.66
Rotation matrix 
 [[ 0.997  0.001 -0.081]
 [ 0.008  0.994  0.106]
 [ 0.081 -0.107  0.991]]
 
Orbit 3
Radius 1.20, angular freq. 4.78
Euler angles 0.17, -0.09 and 0.00
Start time 0.87
Rotation matrix 
 [[ 0.996 -0.    -0.087]
 [-0.015  0.985 -0.17 ]
 [ 0.086  0.171  0.982]]
 
Orbit 4
Radius 1.50, angular freq. 3.42
Euler angles -0.06, -0.17 and -0.00
Start time 0.87
Rotation matrix 
 [[ 0.985  0.    -0.172]
 [ 0.011  0.998  0.062]
 [ 0.172 -0.063  0.9